In [1]:
import sys
sys.path.append("../")

In [97]:
import hashlib

In [2]:
from db import get_connection
from typing import List, Tuple
class AudioHashh:
  def __init__(self):
    pass

  @classmethod
  def create_table(cls):
    conn = get_connection()
    sql = """
    CREATE TABLE IF NOT EXISTS audio_hash (
        id serial PRIMARY KEY,
        key TEXT NOT NULL,
        minhash TEXT NOT NULL,
        name TEXT NOT NULL,
        frame INTEGER NOT NULL  
      )
    """
    conn.cursor().execute(sql)
    conn.commit()
  
  def insertMany(self, data):
    conn = get_connection()
    sql = "INSERT INTO audio_hash (id, key, minhash, name, frame) VALUES (DEFAULT, %s, %s, %s, %s)"
    conn.cursor().executemany(sql, data)
    conn.commit()
    
  def getMinHash(self, band)->List[Tuple[str,str,str,int]]:
    conn = get_connection()
    sql = """
    SELECT key, minhash, name, frame FROM audio_hash WHERE key in %s
    """
    cur = conn.cursor()
    cur.execute(sql, (band,))
    minhash = cur.fetchall()
    cur.close()
    conn.close()
    return minhash

In [313]:
import numpy as np
import random
from models.audio.AudioHashModel import AudioHash
import scipy.stats as stats

class MinHash:
  def __init__(self, num_perm, seed=333):
    self.permutations = self._permutations_generate(num_perm, seed)
  
  def _permutations_generate(self, num_perm, seed=333)->list:
    np.random.seed(seed)
    permutations = []
    for _ in range(num_perm):
      res = np.random.choice( 255, 100,replace=False)
      while stats.entropy(res) < 5:
        res = np.random.choice( 255, 100,replace=False)
      print("APPEND")
      permutations.append(res) 
    return permutations
      
  def hash(self,array)->list:
    signature = []
    for permutation in self.permutations:
      for j in permutation:
        if(array[j] > 0):
          signature.append(j)
          break
    return signature
  
  def jaccard_similarity(self,signature1, signature2):
    intersection = np.sum(np.bitwise_and(signature1, signature2))
    union = np.sum(np.bitwise_or(signature1, signature2))
    return intersection / union 

class LsH:
    def __init__(self, threshold:float,seed:int = 3267,num_hash_functions:int = 100,bands:int = 25, rows:int = 4):
      assert threshold > 0 and threshold < 1
      assert bands*rows == num_hash_functions
      self._threshold = threshold
      self._num_hash_functions = num_hash_functions
      self._bands = bands
      self._rows = rows
      self._min_hash = MinHash(num_hash_functions, seed)
      self._buckets = {}
    
    def clear(self):
      self._buckets.clear()

    def searchFingerprints(self, fingerprints):
      compared_sketches = set()
      #N x 32 x 128
      for i,fs in enumerate(fingerprints):
        for j,f in enumerate(fs):
          for key,bucket in self._buckets.items():
            k = ''.join(map(str, f))
            if k  in bucket and k + key not in compared_sketches:
              compared_sketches.add(k+key)
              for sims in bucket[k]:
                if len(sims[0]) == len(fs):
                  jac = self._min_hash.jaccard_similarity(sims[0], fs)
                  if jac >= self._threshold:print((key,( sims[1] * (128*64/5512))/60,((i+j)*(128*64/5512))/60, jac)) 
            
      
    def addFingerprints(self, fingerprints,name):
        mapper = {}
        #N x 32 x 128
        for i,fs in enumerate(fingerprints):
          for j,f in enumerate(fs):
            key = ''.join(map(str, f))
            if key not in mapper:
              mapper[key] = []
            mapper[key].append((fs,i,j))
        
        self._buckets[name] = mapper
              
          
    
    def searchInDb(self, fingerprints,audioHashes:AudioHash,name,time):
        min_hashes = self._min_hash.hash(fingerprints)
        band_hashes = []
        compared_sketches = set()
        
        if(len(min_hashes) != self._num_hash_functions):
          return None
        
        
        for i in range(self._bands):
          band_hashes.append(self._compute_band_hash(min_hashes, i))
        dbHashes = audioHashes.getMinHash(tuple(band_hashes))
        
        for dbHashTuple in dbHashes:
          if dbHashTuple[0] in compared_sketches:
            continue
          dbHash = list(map(int, dbHashTuple[1].split(",")))
          jac = self._min_hash.jaccard_similarity(dbHash, min_hashes)
          if jac >= self._threshold:
            return (time, dbHashTuple[0], dbHashTuple[2], dbHashTuple[3], jac)
          compared_sketches.add(dbHashTuple[0])
          
    def search(self, fingerprints,name,time, add_to_bucket = True)->tuple :
        min_hashes = self._min_hash.hash(fingerprints)
        band_hashes = []
        compared_sketches = set()
        
        if(len(min_hashes) != self._num_hash_functions):
          return None
        
        
        for i in range(self._bands):
          band_hashes.append(self._compute_band_hash(min_hashes, i))
          if band_hashes[i] in self._buckets:
            for sketch_to_check in self._buckets[band_hashes[i]]:
              check_key = ''.join(str(x) for x in sketch_to_check)
              if check_key not in compared_sketches:
                jac = self._min_hash.jaccard_similarity(sketch_to_check[0], min_hashes)
                if jac >= self._threshold:
                  return (sketch_to_check[0],sketch_to_check[1],sketch_to_check[2], jac)
                compared_sketches.add(check_key)
                
        if add_to_bucket and len(min_hashes) == self._num_hash_functions:
          for i in range(self._bands):
            if band_hashes[i] not in self._buckets:
              self._buckets[band_hashes[i]] = []
            self._buckets[band_hashes[i]].append((min_hashes, name, time))
            
    def add(self, fingerprints, name, time):
        min_hashes = self._min_hash.hash(fingerprints)
        band_hashes = []
        if(len(min_hashes) != self._num_hash_functions):
          return None
        
        for i in range(self._bands):
          band_hashes.append(self._compute_band_hash(min_hashes, i))
          if band_hashes[i] not in self._buckets:
            self._buckets[band_hashes[i]] = []
          self._buckets[band_hashes[i]].append((min_hashes, name, time))
          
    def _compute_band_hash(self, min_hashes: list, i: int) -> str:
        """Compute a hash for quick bucket match search."""
        band_hash_list = []
        for j in range(self._rows):
            # Adding the rows corresponding to ith band
            band_hash_list.append(str(min_hashes[i * self._rows + j]))
        return hashlib.md5(''.join(band_hash_list).encode('utf-8')).hexdigest()


    def get_min_hash(self):
      return self._min_hash
      

In [4]:
from libs.ContentDataSet import ContentDataset

In [5]:
valDataset = ContentDataset("../data/compressed_val/")

In [6]:
licDataset = ContentDataset("../data/test/")

In [314]:
audioLSH = LsH(threshold=0.82,seed=156)

KeyboardInterrupt: 

In [169]:
videoLSH = LsH(threshold=0.8,seed=33)

In [155]:
audio1 = valDataset.content_list[0][1]
audio2 = licDataset.content_list[0][1]

In [156]:
video1 = valDataset.content_list[0][2]
video2 = licDataset.content_list[0][2]

In [170]:
for i,a in enumerate(video2[:-1]):
  videoLSH.add(a,"Licence",i)
  
for i,a in enumerate(video1[:-1]):
  res = videoLSH.search(a,"Pirate",i,add_to_bucket = False)
  if(res != None):
    print((i*2)/60,(res[2]*2)/60,res[3])

3.2333333333333334 0.0 1.0
8.9 0.0 1.0


In [173]:
for i,a in enumerate(audio2[:-1]):
  audioLSH.add(a,"Licence",i)

for i,a in enumerate(audio1[:-1]):
  res = audioLSH.search(a,"Pirate",i,add_to_bucket = False)
  if(res != None):
    print((i*1.48)/60,(res[2]*1.48)/60,res[3])


0.0 4.6866666666666665 0.8201000205521682
9.842 14.06 0.850494233937397
10.729999999999999 12.062000000000001 0.8260744985673353


In [312]:
import scipy.stats as sp

array = [ 1670, 2562, 2370, 4099, 610, 624, 2703, 8003, 5070,
                                                        7428, 6463, 3397, 1418, 4961, 6837, 3754, 6427,
                                                        6808, 3246, 2514, 7587, 1541, 4982, 1809, 6701,
                                                        1486, 7869, 548, 5615, 6399, 1200, 557, 1014, 2928,
                                                        907, 910, 4252, 2955, 4605, 3654, 6129, 6604, 2162,
                                                        738, 7084, 4652, 1433, 358, 2005, 2845, 3851, 5931,
                                                        491, 3057, 2209, 595, 1037, 7364, 6284, 711, 5818,
                                                        4278, 4486, 1995, 5422, 6166, 8177, 242, 3067, 3658,
                                                        6212, 5548, 2321, 7105, 4783, 3090, 2557, 774, 5786,
                                                        2130, 7678, 7002, 6386, 8183, 3453, 4157, 1013,
                                                        7053, 5592, 5499, 3147, 5192, 980, 2747, 5838, 3588,
                                                        1782, 5594, 5189, 2722, 4010, 7286, 5659, 4300, 195,
                                                        3942, 570, 6065, 2843, 1161, 3723, 8065, 245, 6066,
                                                        7147, 5741, 2278, 7823, 2127, 1434, 112, 1456, 2987,
                                                        6596, 4640, 7115, 2677, 141, 6910, 3514, 2062, 1337,
                                                        7076, 6152, 7541, 2153, 3928, 3113, 3337, 3077,
                                                        1012, 421, 3144, 2211, 40, 6181, 17, 3968, 2238,
                                                        182, 1060, 6295, 600, 2488, 3140, 6581, 7682, 2349,
                                                        2310, 4596, 520, 3302, 3247, 3732, 7979, 3431, 167,
                                                        3983, 979, 632, 2914, 1083, 3192, 3275, 5135, 2651,
                                                        3226, 7523, 7851, 4559, 5448, 1299, 3903, 453, 3454,
                                                        2685, 4183, 4987, 2915, 2762, 7301, 2861, 849, 8153,
                                                        3731, 8031, 4921, 1397, 5794, 6862, 2581, 484, 2713,
                                                        3537, 6625, 6550, 5306, 2053, 7451, 5074, 7579,
                                                        2163, 1545, 1640, 7045, 967, 2624, 3387, 2475, 2042,
                                                        3520, 7455, 817, 1429, 3813, 1150, 5939, 8181, 5154,
                                                        603, 2172, 5565, 2165, 5911, 3580, 5545, 2480, 1583,
                                                        6383, 4464, 5692, 3137, 821, 7263, 3600, 2590, 6190,
                                                        6294, 3729, 7957, 7509, 1615, 6977, 3422, 5888]

entriopy = sp.entropy(np.random.choice( 5555, 100,replace=False))
entriopy 

4.410897068193597

In [65]:
av = np.array(video1[:-1])
av = av.reshape((av.shape[0],128,72))
bv = np.array(video2[:-1])
bv = bv.reshape((bv.shape[0],128,72))

In [10]:
a = np.array(audio1[:-1])
a = a.reshape((a.shape[0],128,32))
b = np.array(audio2[:-1])
b = b.reshape((b.shape[0],128,32))

In [23]:
a.shape, b.shape

((534, 128, 32), (1197, 128, 32))

In [67]:
videoLSH.addFingerprints(bv,"Licence")

In [68]:
print(videoLSH.searchFingerprints(bv))

('Licence', 0.0, 0.0, 1.0)
('Licence', 0.0, 0.0, 1.0)
('Licence', 0.0, 0.0, 1.0)
('Licence', 0.0, 0.0, 1.0)
('Licence', 0.0, 0.0, 1.0)
('Licence', 0.0, 0.0, 1.0)
('Licence', 0.0, 0.0, 1.0)
('Licence', 0.0, 0.0, 1.0)
('Licence', 0.0, 0.0, 1.0)
('Licence', 0.0, 0.0, 1.0)
('Licence', 0.0, 0.0, 1.0)
('Licence', 0.0, 0.0, 1.0)
('Licence', 0.0, 0.0, 1.0)
('Licence', 0.0, 0.0, 1.0)
('Licence', 0.0, 0.0, 1.0)
('Licence', 0.0, 0.0, 1.0)
('Licence', 0.0, 0.0, 1.0)
('Licence', 0.0, 0.0, 1.0)
('Licence', 0.0, 0.0, 1.0)
('Licence', 0.0, 0.0, 1.0)
('Licence', 0.0, 0.0, 1.0)
('Licence', 0.0, 0.0, 1.0)
('Licence', 0.0, 0.0, 1.0)
('Licence', 0.0, 0.0, 1.0)
('Licence', 0.0, 0.0, 1.0)
('Licence', 0.0, 0.0, 1.0)
('Licence', 0.0, 0.0, 1.0)
('Licence', 0.0, 0.0, 1.0)
('Licence', 0.0, 0.0, 1.0)
('Licence', 0.0, 0.0, 1.0)
('Licence', 0.0, 0.0, 1.0)
('Licence', 0.0, 0.0, 1.0)
('Licence', 0.0, 0.0, 1.0)
('Licence', 0.0, 0.0, 1.0)
('Licence', 0.0, 0.0, 1.0)
('Licence', 0.0, 0.0, 1.0)
('Licence', 0.0, 0.0, 1.0)
(

KeyboardInterrupt: 

In [61]:
audioLSH.addFingerprints(b,"Licence")

In [62]:
print(audioLSH.searchFingerprints(b))

('Licence', 0.0, 0.0, 1.0)
('Licence', 0.0, 0.0, 1.0)
('Licence', 0.0, 0.024770198355104016, 1.0)
('Licence', 0.0, 0.024770198355104016, 1.0)
('Licence', 0.0, 0.04954039671020803, 1.0)
('Licence', 0.0, 0.07431059506531204, 1.0)
('Licence', 0.0, 0.09908079342041606, 1.0)
('Licence', 0.0, 0.12385099177552009, 1.0)
('Licence', 0.0, 0.14862119013062408, 1.0)
('Licence', 0.0, 0.1733913884857281, 1.0)
('Licence', 0.0, 0.1733913884857281, 1.0)
('Licence', 0.0, 0.19816158684083213, 1.0)
('Licence', 0.0, 0.19816158684083213, 1.0)
('Licence', 0.0, 0.22293178519593615, 1.0)
('Licence', 0.0, 0.24770198355104017, 1.0)
('Licence', 0.0, 0.27247218190614414, 1.0)
('Licence', 0.0, 0.27247218190614414, 1.0)
('Licence', 0.0, 0.29724238026124816, 1.0)
('Licence', 0.0, 0.29724238026124816, 1.0)
('Licence', 0.0, 0.29724238026124816, 1.0)
('Licence', 0.0, 0.29724238026124816, 1.0)
('Licence', 0.0, 0.3220125786163522, 1.0)
('Licence', 0.0, 0.3467827769714562, 1.0)
('Licence', 0.0, 0.3467827769714562, 1.0)
('L

In [13]:
audio1Spec = valDataset.content_list[0][3]

In [14]:
audio1.__len__()

535

In [15]:
video1 = valDataset.content_list[0][2]
video2 = licDataset.content_list[0][2]

In [16]:
for k,f in enumerate(audio2[:-1]):
  audioLSH.search(f,"Licence",k)

In [17]:
def getSpecificFingerprint(mel_spec,start,end):
  def get_energy_spec(spec):
    # Transpose 'spec' upfront and get the shifted versions for calculations
    specT = spec.T
    specT_shifted_vertically = np.roll(specT, shift=-1, axis=0)
    specT_shifted_horizontally = np.roll(specT, shift=-1, axis=1)

    # Calculate the differences for current and previous rows
    diff_current = specT - specT_shifted_horizontally
    diff_previous = specT_shifted_vertically - np.roll(specT_shifted_horizontally, shift=-1, axis=0)

    # Compute the energy_spec matrix using NumPy's greater function for element-wise comparison
    energy_spec = np.greater(diff_current - diff_previous, 0).astype(int)
    return energy_spec.T
  def get_audio_fingerprint(spec):
    fingerprint = []
    energy_spec = get_energy_spec(spec)
    for i in range(0,energy_spec.shape[1],128):
      fingerprint.append(energy_spec[:,i:i+128].flatten())
    return fingerprint 
  return get_audio_fingerprint(mel_spec[:,start:end])
  
   

In [18]:
fragments =[]
for k,f in enumerate(audio1[:-1]):
  res = audioLSH.search(f,"Pirate",k,add_to_bucket = False)
  if res != None:
    fragments.append((k,res[0],res[1],res[2],res[3]))
    print(k*1.48/60,"|",res[2]*1.48/60,"|",res[1],"|",res[3])

0.0 | 0.37 | Licence | 0.5458196247186127
0.024666666666666667 | 0.12333333333333334 | Licence | 0.45043865881842593
0.04933333333333333 | 0.12333333333333334 | Licence | 0.557206799732146
0.074 | 7.696 | Licence | 0.479114499940045
0.09866666666666667 | 0.37 | Licence | 0.5603554450968209
0.12333333333333334 | 0.19733333333333333 | Licence | 0.46731561953155315
0.148 | 1.9486666666666668 | Licence | 0.5308031078806975
0.17266666666666666 | 0.9126666666666666 | Licence | 0.4700586364722534
0.19733333333333333 | 0.024666666666666667 | Licence | 0.49413768845607403
0.222 | 1.9486666666666668 | Licence | 0.4776557375882993
0.24666666666666667 | 0.222 | Licence | 0.4929153062707604
0.27133333333333337 | 1.9486666666666668 | Licence | 0.4836828203709023
0.296 | 12.358 | Licence | 0.4935203648154249
0.32066666666666666 | 7.696 | Licence | 0.5255441475446868
0.3453333333333333 | 7.696 | Licence | 0.49631740997121077
0.37 | 0.222 | Licence | 0.5838565308896547
0.39466666666666667 | 0.172666666

In [19]:
minHash = audioLSH.get_min_hash()
#10 sec interval in our frames
interval = 30
for i, v in enumerate(fragments):
  start = int(v[0]) - interval
  end = int(v[0]) + interval
  if start < 0:
    start = 0
  #audio1 is fingerprint of the original audio
  if end > len(audio1):
    end = len(audio1)
  
  print(start,end)
  for j in range(start,end):
    newFingerprint = getSpecificFingerprint(audio1Spec,j,end)
    for k,f in enumerate(newFingerprint[:-1]):
      res = audioLSH.search(f,"Pirate",k,add_to_bucket = False)
      if res != None:
        fragments.append((k,res[0],res[1],res[2],res[3]))
        print(k*1.48/60,res[1],res[2]*1.48/60,res[3])
  

0 30
0 31
0 32
0 33
0 34
0 35
0 36
0 37
0 38
0 39
0 40
0 41
0 42
0 43
0 44
0 45
0 46
0 47
0 48
0 49
0 50
0 51
0 52
0 53
0 54
0 55
0 56
0 57
0 58
0 59
0 60
1 61
2 62
3 63
4 64
5 65
6 66
7 67
8 68
9 69
10 70
11 71
12 72
13 73
14 74
15 75
16 76
17 77
18 78
19 79
20 80
21 81
22 82
23 83
24 84
25 85
26 86
27 87
28 88
29 89
30 90
31 91
32 92
33 93
34 94
35 95
36 96
37 97
38 98
39 99
40 100
41 101
42 102
43 103
44 104
45 105
46 106
47 107
48 108
49 109
50 110
51 111
52 112
53 113
54 114
55 115
56 116
57 117
58 118
59 119
60 120
61 121
62 122
63 123
64 124
65 125
66 126
67 127
68 128
69 129
70 130
71 131
72 132
73 133
74 134
75 135
76 136
77 137
78 138
79 139
80 140
81 141
82 142
83 143
84 144
85 145
86 146
87 147
88 148
89 149
90 150
91 151
92 152
93 153
94 154
95 155
96 156
97 157
98 158
99 159
100 160
101 161
102 162
103 163
104 164
105 165
106 166
107 167
108 168
109 169
110 170
111 171
112 172
113 173
114 174
115 175
116 176
117 177
118 178
119 179
120 180
121 181
122 182
123 183
124 184


In [20]:
for k,f in enumerate(video2):
  videoLSH.search(f,"Licence",k)

In [21]:
for k,f in enumerate(video1):
  res = videoLSH.search(f,"Pirate",k,add_to_bucket = False)
  if res != None:
    print(k*2/60,res[1],res[2]*2/60,res[3])

0.5 Licence 5.9 0.7207620297610033
2.9 Licence 7.666666666666667 0.6520182071044577
3.2333333333333334 Licence 0.0 1.0
5.866666666666666 Licence 5.7 0.6771011779665507
6.366666666666666 Licence 0.7666666666666667 0.6593157568954121
8.9 Licence 0.0 1.0
